In [1]:
# Importing Required Python Packages
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
pd.set_option('display.max_columns',None)

In [2]:
# Loading Reduced feature Training set
X_train_red = pd.read_csv('X_train_final.csv')
y_train = pd.read_csv('y_train.final.csv')

In [3]:
# Loading Reduced feature Test set
X_test_red = pd.read_csv('X_test_final.csv')
y_test = pd.read_csv('y_test.final.csv')

## Model_11:  Keras Variable Layer Dense Model With SELU Activation & Alpha_Dropout layer

In [4]:
# Importing Optuna , Tensorflow & Keras
import optuna , tensorflow as tf

In [5]:
# Importing Keras
from tensorflow import keras

In [6]:
# Importing train test split from Sklearn to produce validation set
from sklearn.model_selection import train_test_split

In [7]:
# Importing the Sklearn's roc_auc_score module
from sklearn.metrics import roc_auc_score

In [8]:
# Performing train validation split with test size = .1 to provide more Training data to Neural Net
X_train_red_1, X_val, y_train_1, y_val = train_test_split(X_train_red, y_train, test_size=0.1, random_state=42,
                                                          stratify=y_train)

In [9]:
# defining class weight dictionary list for the imbalanced class
cl_weight = [{0:1.0,1:7.8761},{0:1.0,1:9.0},{0:1.0,1:10.0},{0:1.0,1:11.0},{0:1.0,1:12.0},{0:1.0,1:13.0},{0:1.0,1:14.0}]

In [10]:
# Defining best roc_auc score
best_roc_auc = 0

In [15]:
# defining the objective function
def objective_wrappper_dropout(X_tr, y_tr, X_val, y_val, cl_weight):
    '''
    Optimizes Keras dropout layer model's best parameters on the given training set: X_tr,y_tr
    using validation set: X_val,y_val & class weights: cl_weight
    '''

   
    
    def objective(trial):
        s = trial.suggest_int('step',2,5)
        def exponential_decay_fn(epoch):
            return 0.01 * 0.1**(epoch /s )
        
        # building model & searching for the best no. of neural units per layer.
        model = keras.models.Sequential()
        model.add(keras.layers.InputLayer(input_shape=X_tr.shape[1:]))
        for i in range(trial.suggest_int('number',3,7)):
            model.add(keras.layers.Dense(units=trial.suggest_int('units_{}'.format(i),100,500),activation='selu',
                                     kernel_initializer='lecun_normal')) # For self normalization
        model.add(keras.layers.AlphaDropout(rate=0.2))
        model.add(keras.layers.Dense(units=1,activation='sigmoid'))
    
            
        # Compiling the model
        model.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])
    
        # Defining the Callbacks
        checkpoint_cb = keras.callbacks.ModelCheckpoint('best_model.h5',save_best_only=True) # 1st Callback
        early_stopping_cb = keras.callbacks.EarlyStopping(patience=10) # 2nd Callback, Stop if validation score doen't improve for
        # 10 epochs        
        lr_scheduler_cb = keras.callbacks.LearningRateScheduler(exponential_decay_fn)# 3rd Callback
        
        #Fitting the model
        model.fit(X_tr,y_tr,epochs=50,validation_data=(X_val,y_val),batch_size=32,
             class_weight=trial.suggest_categorical('best_weight',cl_weight),
             callbacks=[checkpoint_cb,early_stopping_cb,lr_scheduler_cb])#,tensorboard_cb])
    
        # Loading the best model 
        model_best = keras.models.load_model('best_model.h5')
    
        # Computing the roc_auc_score for the validation set
        roc_auc_1 = roc_auc_score(y_val,model_best.predict(X_val))
        global best_roc_auc
        # Updating best_roc_auc score
        if roc_auc_1 > best_roc_auc:
            best_roc_auc = roc_auc_1
            model_best.save('Best_model_Selu_dropout_learn.h5')
        
        return roc_auc_1
    
    return objective
    

In [16]:
# Defining the evaluation function for study's best parameters
def train_test_roc_auc(X_tr, y_tr, X_v, y_v, obj_func, cl_weight,n_trials=100):
    ''' Computes the best hyper parameters of the Neural net using the Training set(X_tr,y_tr) & Validation set
    (X_v,y_v), class weights cl_wei & 
    returns Optuna's study's best score & clasifier parameters'''
    
    study = optuna.create_study(direction='maximize')
    study.optimize(obj_func(X_tr, y_tr, X_v, y_v, cl_weight), n_trials)
    best_score = study.best_value
    best_params = study.best_params
    return (best_score,best_params)


In [17]:
# Extracting the best model parameters and best study score
best_study_score,best_study_params = train_test_roc_auc(X_train_red_1, y_train_1, X_val, y_val, objective_wrappper_dropout, cl_weight)

[I 2020-10-07 23:05:14,173] A new study created in memory with name: no-name-79c07e29-5cbf-40fa-841d-eb451e2c4f22


  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 29655 samples, validate on 3295 samples
Epoch 1/50
29655/29655 [==============================] - ETA: 17:13 - loss: 2.4513 - accuracy: 0.343 - ETA: 1:22 - loss: 34.0392 - accuracy: 0.476 - ETA: 40s - loss: 17.8668 - accuracy: 0.568 - ETA: 26s - loss: 12.0734 - accuracy: 0.57 - ETA: 20s - loss: 9.4383 - accuracy: 0.5904 - ETA: 16s - loss: 7.7784 - accuracy: 0.621 - ETA: 14s - loss: 6.6593 - accuracy: 0.621 - ETA: 12s - loss: 5.9188 - accuracy: 0.604 - ETA: 11s - loss: 5.3873 - accuracy: 0.605 - ETA: 9s - loss: 4.9389 - accuracy: 0.605 - ETA: 9s - loss: 4.5985 - accuracy: 0.60 - ETA: 8s - loss: 4.2830 - accuracy: 0.60 - ETA: 7s - loss: 4.0239 - accuracy: 0.60 - ETA: 7s - loss: 3.8578 - accuracy: 0.60 - ETA: 6s - loss: 3.6829 - accuracy: 0.60 - ETA: 6s - loss: 3.5579 - accuracy: 0.59 - ETA: 5s - loss: 3.4584 - accuracy: 0.59 - ETA: 5s - loss: 3.3627 - accuracy: 0.58 - ETA: 5s - loss: 3.2801 - accuracy: 0.59 - ETA: 5s - loss: 3.19

29655/29655 [==============================] - ETA: 5s - loss: 1.2850 - accuracy: 0.09 - ETA: 4s - loss: 1.2841 - accuracy: 0.09 - ETA: 3s - loss: 1.4176 - accuracy: 0.11 - ETA: 3s - loss: 1.3969 - accuracy: 0.11 - ETA: 3s - loss: 1.3894 - accuracy: 0.11 - ETA: 3s - loss: 1.4178 - accuracy: 0.11 - ETA: 3s - loss: 1.4084 - accuracy: 0.11 - ETA: 3s - loss: 1.4086 - accuracy: 0.11 - ETA: 3s - loss: 1.4066 - accuracy: 0.11 - ETA: 2s - loss: 1.4083 - accuracy: 0.11 - ETA: 2s - loss: 1.4155 - accuracy: 0.11 - ETA: 2s - loss: 1.4080 - accuracy: 0.11 - ETA: 2s - loss: 1.4083 - accuracy: 0.11 - ETA: 2s - loss: 1.4110 - accuracy: 0.11 - ETA: 2s - loss: 1.4104 - accuracy: 0.11 - ETA: 2s - loss: 1.4072 - accuracy: 0.11 - ETA: 2s - loss: 1.4081 - accuracy: 0.11 - ETA: 2s - loss: 1.4177 - accuracy: 0.11 - ETA: 2s - loss: 1.4135 - accuracy: 0.11 - ETA: 2s - loss: 1.4102 - accuracy: 0.11 - ETA: 2s - loss: 1.4023 - accuracy: 0.11 - ETA: 2s - loss: 1.4013 - accuracy: 0.11 - ETA: 2s - loss: 1.4004 - accu

29655/29655 [==============================] - ETA: 3s - loss: 1.4437 - accuracy: 0.12 - ETA: 3s - loss: 1.4633 - accuracy: 0.12 - ETA: 3s - loss: 1.4690 - accuracy: 0.13 - ETA: 3s - loss: 1.4335 - accuracy: 0.12 - ETA: 3s - loss: 1.4071 - accuracy: 0.11 - ETA: 3s - loss: 1.4228 - accuracy: 0.12 - ETA: 2s - loss: 1.4175 - accuracy: 0.11 - ETA: 2s - loss: 1.4135 - accuracy: 0.11 - ETA: 2s - loss: 1.4015 - accuracy: 0.11 - ETA: 2s - loss: 1.4097 - accuracy: 0.11 - ETA: 2s - loss: 1.4148 - accuracy: 0.11 - ETA: 2s - loss: 1.4011 - accuracy: 0.11 - ETA: 2s - loss: 1.4045 - accuracy: 0.11 - ETA: 2s - loss: 1.4049 - accuracy: 0.11 - ETA: 2s - loss: 1.4037 - accuracy: 0.11 - ETA: 2s - loss: 1.4036 - accuracy: 0.11 - ETA: 2s - loss: 1.3988 - accuracy: 0.11 - ETA: 2s - loss: 1.3931 - accuracy: 0.11 - ETA: 2s - loss: 1.3918 - accuracy: 0.11 - ETA: 2s - loss: 1.3985 - accuracy: 0.11 - ETA: 2s - loss: 1.3976 - accuracy: 0.11 - ETA: 2s - loss: 1.3922 - accuracy: 0.11 - ETA: 2s - loss: 1.3907 - accu

29655/29655 [==============================] - ETA: 3s - loss: 2.0704 - accuracy: 0.25 - ETA: 3s - loss: 1.3555 - accuracy: 0.10 - ETA: 3s - loss: 1.3548 - accuracy: 0.10 - ETA: 3s - loss: 1.3296 - accuracy: 0.10 - ETA: 3s - loss: 1.3400 - accuracy: 0.10 - ETA: 3s - loss: 1.3547 - accuracy: 0.10 - ETA: 2s - loss: 1.3573 - accuracy: 0.10 - ETA: 2s - loss: 1.3728 - accuracy: 0.11 - ETA: 2s - loss: 1.3883 - accuracy: 0.11 - ETA: 2s - loss: 1.3875 - accuracy: 0.11 - ETA: 2s - loss: 1.4005 - accuracy: 0.11 - ETA: 2s - loss: 1.3872 - accuracy: 0.11 - ETA: 2s - loss: 1.3841 - accuracy: 0.11 - ETA: 2s - loss: 1.3879 - accuracy: 0.11 - ETA: 2s - loss: 1.3919 - accuracy: 0.11 - ETA: 2s - loss: 1.3911 - accuracy: 0.11 - ETA: 2s - loss: 1.3843 - accuracy: 0.11 - ETA: 2s - loss: 1.3773 - accuracy: 0.11 - ETA: 2s - loss: 1.3775 - accuracy: 0.11 - ETA: 2s - loss: 1.3838 - accuracy: 0.11 - ETA: 2s - loss: 1.3826 - accuracy: 0.11 - ETA: 2s - loss: 1.3825 - accuracy: 0.11 - ETA: 2s - loss: 1.3824 - accu

...

  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 29655 samples, validate on 3295 samples
Epoch 1/50
29655/29655 [==============================] - ETA: 11:26 - loss: 1.7599 - accuracy: 0.562 - ETA: 42s - loss: 5.1154 - accuracy: 0.4412  - ETA: 20s - loss: 3.4434 - accuracy: 0.440 - ETA: 13s - loss: 2.8291 - accuracy: 0.465 - ETA: 10s - loss: 2.5445 - accuracy: 0.491 - ETA: 8s - loss: 2.3375 - accuracy: 0.492 - ETA: 7s - loss: 2.2394 - accuracy: 0.49 - ETA: 6s - loss: 2.1492 - accuracy: 0.48 - ETA: 5s - loss: 2.0492 - accuracy: 0.50 - ETA: 5s - loss: 2.0047 - accuracy: 0.51 - ETA: 4s - loss: 1.9705 - accuracy: 0.51 - ETA: 4s - loss: 1.9579 - accuracy: 0.51 - ETA: 4s - loss: 1.9116 - accuracy: 0.52 - ETA: 3s - loss: 1.9187 - accuracy: 0.52 - ETA: 3s - loss: 1.9059 - accuracy: 0.52 - ETA: 3s - loss: 1.8642 - accuracy: 0.53 - ETA: 3s - loss: 1.8608 - accuracy: 0.53 - ETA: 2s - loss: 1.8635 - accuracy: 0.53 - ETA: 2s - loss: 1.8639 - accuracy: 0.53 - ETA: 2s - loss: 1.8846 - accur

29655/29655 [==============================] - ETA: 3s - loss: 1.4226 - accuracy: 0.81 - ETA: 3s - loss: 1.2198 - accuracy: 0.77 - ETA: 2s - loss: 1.1771 - accuracy: 0.77 - ETA: 2s - loss: 1.2085 - accuracy: 0.74 - ETA: 2s - loss: 1.2452 - accuracy: 0.71 - ETA: 2s - loss: 1.2447 - accuracy: 0.70 - ETA: 2s - loss: 1.2464 - accuracy: 0.70 - ETA: 2s - loss: 1.2480 - accuracy: 0.71 - ETA: 2s - loss: 1.2440 - accuracy: 0.71 - ETA: 2s - loss: 1.2389 - accuracy: 0.71 - ETA: 2s - loss: 1.2333 - accuracy: 0.71 - ETA: 1s - loss: 1.2393 - accuracy: 0.72 - ETA: 1s - loss: 1.2328 - accuracy: 0.72 - ETA: 1s - loss: 1.2372 - accuracy: 0.72 - ETA: 1s - loss: 1.2373 - accuracy: 0.72 - ETA: 1s - loss: 1.2479 - accuracy: 0.71 - ETA: 1s - loss: 1.2365 - accuracy: 0.71 - ETA: 1s - loss: 1.2427 - accuracy: 0.71 - ETA: 1s - loss: 1.2416 - accuracy: 0.71 - ETA: 1s - loss: 1.2411 - accuracy: 0.71 - ETA: 1s - loss: 1.2438 - accuracy: 0.71 - ETA: 1s - loss: 1.2538 - accuracy: 0.70 - ETA: 1s - loss: 1.2522 - accu

29655/29655 [==============================] - ETA: 3s - loss: 1.1940 - accuracy: 0.68 - ETA: 2s - loss: 1.1479 - accuracy: 0.74 - ETA: 2s - loss: 1.1826 - accuracy: 0.75 - ETA: 2s - loss: 1.2120 - accuracy: 0.75 - ETA: 2s - loss: 1.1563 - accuracy: 0.76 - ETA: 2s - loss: 1.1642 - accuracy: 0.76 - ETA: 2s - loss: 1.1473 - accuracy: 0.76 - ETA: 2s - loss: 1.1495 - accuracy: 0.76 - ETA: 2s - loss: 1.1536 - accuracy: 0.77 - ETA: 2s - loss: 1.1830 - accuracy: 0.76 - ETA: 1s - loss: 1.1918 - accuracy: 0.76 - ETA: 1s - loss: 1.1841 - accuracy: 0.76 - ETA: 1s - loss: 1.1942 - accuracy: 0.75 - ETA: 1s - loss: 1.1991 - accuracy: 0.75 - ETA: 1s - loss: 1.2065 - accuracy: 0.75 - ETA: 1s - loss: 1.2078 - accuracy: 0.75 - ETA: 1s - loss: 1.2051 - accuracy: 0.75 - ETA: 1s - loss: 1.2057 - accuracy: 0.75 - ETA: 1s - loss: 1.2067 - accuracy: 0.75 - ETA: 1s - loss: 1.2081 - accuracy: 0.74 - ETA: 1s - loss: 1.2096 - accuracy: 0.74 - ETA: 1s - loss: 1.2088 - accuracy: 0.74 - ETA: 1s - loss: 1.2119 - accu

29655/29655 [==============================] - ETA: 3s - loss: 1.0571 - accuracy: 0.59 - ETA: 2s - loss: 1.1411 - accuracy: 0.72 - ETA: 2s - loss: 1.1884 - accuracy: 0.73 - ETA: 2s - loss: 1.2464 - accuracy: 0.72 - ETA: 2s - loss: 1.2377 - accuracy: 0.73 - ETA: 2s - loss: 1.2193 - accuracy: 0.73 - ETA: 2s - loss: 1.2025 - accuracy: 0.73 - ETA: 2s - loss: 1.2120 - accuracy: 0.73 - ETA: 2s - loss: 1.2010 - accuracy: 0.73 - ETA: 2s - loss: 1.2037 - accuracy: 0.73 - ETA: 2s - loss: 1.2246 - accuracy: 0.73 - ETA: 2s - loss: 1.2220 - accuracy: 0.72 - ETA: 1s - loss: 1.2302 - accuracy: 0.73 - ETA: 1s - loss: 1.2256 - accuracy: 0.72 - ETA: 1s - loss: 1.2121 - accuracy: 0.73 - ETA: 1s - loss: 1.2033 - accuracy: 0.73 - ETA: 1s - loss: 1.2017 - accuracy: 0.73 - ETA: 1s - loss: 1.1980 - accuracy: 0.73 - ETA: 1s - loss: 1.1961 - accuracy: 0.73 - ETA: 1s - loss: 1.1934 - accuracy: 0.73 - ETA: 1s - loss: 1.1922 - accuracy: 0.73 - ETA: 1s - loss: 1.2029 - accuracy: 0.73 - ETA: 1s - loss: 1.2016 - accu

[I 2020-10-08 00:36:53,682] Trial 99 finished with value: 0.8094254814694637 and parameters: {'step': 5, 'number': 3, 'units_0': 115, 'units_1': 301, 'units_2': 276, 'best_weight': {0: 1.0, 1: 13.0}}. Best is trial 91 with value: 0.8162847850856008.


In [18]:
print('The best roc_auc_score for the study is: ',best_study_score)

The best roc_auc_score for the study is:  0.8162847850856008


In [19]:
print('The best study parameters for the classifier are: ',best_study_params)

The best study parameters for the classifier are:  {'step': 5, 'number': 3, 'units_0': 125, 'units_1': 339, 'units_2': 329, 'best_weight': {0: 1.0, 1: 13.0}}


In [22]:
# loading the best Neural Network
Best_Model_alpha = keras.models.load_model('Best_model_Selu_dropout_learn.h5')

In [23]:
Best_Model_alpha.summary()

Model: "sequential_93"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_427 (Dense)            (None, 125)               4625      
_________________________________________________________________
dense_428 (Dense)            (None, 339)               42714     
_________________________________________________________________
dense_429 (Dense)            (None, 329)               111860    
_________________________________________________________________
alpha_dropout_93 (AlphaDropo (None, 329)               0         
_________________________________________________________________
dense_430 (Dense)            (None, 1)                 330       
Total params: 159,529
Trainable params: 159,529
Non-trainable params: 0
_________________________________________________________________


In [24]:
# Defining the function to calculate the roc_auc score for the feature sets
def cal_roc_auc(X, y, cls, f_set, t_set, model_name):
    ''' Calculates the roc auc score using the best study parameters 
        f_set : String: specifies 'full feature', 'Reduced feature'
        t_set: String: specifies 'training', 'test'
        model_name: String: specifies Name of the model '''
        
    y_pred = cls.predict_proba(X)
    print('The roc_auc_score for the {} {} set using the best {} classifier is '.format(f_set,t_set,model_name),roc_auc_score(y, y_pred))

In [25]:
# Calculating the Reduced feature training set roc_auc score using the pretrained Neural Network having 
# best study parameters & weights
cal_roc_auc(X_train_red, y_train, Best_Model_alpha, 'Reduced feature', 'training', 'Dense Neural Network with Dropout')

The roc_auc_score for the Reduced feature training set using the best Dense Neural Network with Dropout classifier is  0.804127054187866


In [26]:
# Calculating the Reduced feature test set roc_auc score using the pretrained Neural Network having 
# best study parameters & weights
cal_roc_auc(X_test_red, y_test, Best_Model_alpha, 'Reduced feature', 'test', 'Dense Neural Network with Dropout')

The roc_auc_score for the Reduced feature test set using the best Dense Neural Network with Dropout classifier is  0.8040792755554508


### Calculating R_R ratio for Best Dense Neural Network with Alpha_Dropout  layer

In [8]:
# Defining the exponential decay learning rate with step 5.
def exponential_decay_fn(epoch):
            return 0.01 * 0.1**(epoch /5 )

In [9]:
from sklearn.model_selection import StratifiedKFold

In [10]:
# Initializing the K Fold object
cv_strat = StratifiedKFold(10,random_state=42)

In [11]:
# Computing  10 fold  CV predictions on the training set for the Neural Network with dropout layer
scores_neural_dropout = []
for train_index, test_index in cv_strat.split(X_train_red, y_train):
    # Creating  Folds
    X_tr, X_tst = X_train_red.loc[train_index], X_train_red.loc[test_index]
    y_tr, y_tst = y_train.loc[train_index], y_train.loc[test_index]
    
    # Splitting the Training set further into training & validation set.
    X_tr_r, X_val, y_tr_r, y_val = train_test_split(X_tr, y_tr, test_size=0.1, random_state=42, stratify=y_tr)
    
    # Loading fresh best variable layer keras model at every iteration for training on 9 folds
    neural = keras.models.load_model('Best_model_Selu_dropout_learn.h5')
    
    # comiling & Training the Neural Net
    neural.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])
    
    # defining Checkpoints
    checkpoint_cb = keras.callbacks.ModelCheckpoint('best_model.h5',save_best_only=True) # 1st Callback
    early_stopping_cb = keras.callbacks.EarlyStopping(patience=10)# 2nd Callback
    lr_scheduler_cb = keras.callbacks.LearningRateScheduler(exponential_decay_fn)# 3rd Callback
    
    # Fitting The model
    neural.fit(X_tr_r, y_tr_r, epochs=50, validation_data=(X_val,y_val),batch_size=32,
    class_weight={0: 1.0, 1: 13},callbacks=[checkpoint_cb,early_stopping_cb,lr_scheduler_cb])
    
    # Loading the best Neural model after training & before making predictions
    neural_best = keras.models.load_model('best_model.h5')    
    
    # Saving the predictions for every fold in the scores list
    y_pred = neural_best.predict_proba(X_tst)
    scores_neural_dropout.append(roc_auc_score(y_tst,y_pred))
      

  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 26689 samples, validate on 2966 samples
Epoch 1/50
26689/26689 [==============================] - 3s 121us/sample - loss: 2.4167 - accuracy: 0.5591 - val_loss: 1.4011 - val_accuracy: 0.8540
Epoch 2/50
26689/26689 [==============================] - 2s 82us/sample - loss: 1.3544 - accuracy: 0.5907 - val_loss: 1.9049 - val_accuracy: 0.8746
Epoch 3/50
26689/26689 [==============================] - 2s 83us/sample - loss: 1.3300 - accuracy: 0.6170 - val_loss: 1.2948 - val_accuracy: 0.8409
Epoch 4/50
26689/26689 [==============================] - 2s 84us/sample - loss: 1.3038 - accuracy: 0.6440 - val_loss: 1.2838 - val_accuracy: 0.8129
Epoch 5/50
26689/26689 [==============================] - 2s 85us/sample - loss: 1.2744 - accuracy: 0.6611 - val_loss: 1.2395 - val_accuracy: 0.8321
Epoch 6/50
26689/26689 [==============================] - 2s 83us/sample - loss: 1.2707 - accuracy: 0.6683 - val_loss: 1.2176 - val_accuracy: 0.8270
Epoch 

  ...
    to  
  ['...']
  ...
    to  
  ['...']
Train on 26689 samples, validate on 2966 samples
Epoch 1/50
26689/26689 [==============================] - 3s 114us/sample - loss: 2.4267 - accuracy: 0.5642 - val_loss: 2.5864 - val_accuracy: 0.8793
Epoch 2/50
26689/26689 [==============================] - 2s 79us/sample - loss: 1.4419 - accuracy: 0.5833 - val_loss: 2.6087 - val_accuracy: 0.8958
Epoch 3/50
26689/26689 [==============================] - 2s 78us/sample - loss: 1.3532 - accuracy: 0.5771 - val_loss: 1.2764 - val_accuracy: 0.7461
Epoch 4/50
26689/26689 [==============================] - 2s 78us/sample - loss: 1.3027 - accuracy: 0.5952 - val_loss: 1.5474 - val_accuracy: 0.8614
Epoch 5/50
26689/26689 [==============================] - 2s 77us/sample - loss: 1.2911 - accuracy: 0.6161 - val_loss: 1.2933 - val_accuracy: 0.8328
Epoch 6/50
26689/26689 [==============================] - 2s 78us/sample - loss: 1.2815 - accuracy: 0.6095 - val_loss: 1.3123 - val_accuracy: 0.8469
Epoch 

26689/26689 [==============================] - 2s 82us/sample - loss: 1.2218 - accuracy: 0.7769 - val_loss: 1.2657 - val_accuracy: 0.7883
Epoch 16/50
26689/26689 [==============================] - 2s 82us/sample - loss: 1.2200 - accuracy: 0.7683 - val_loss: 1.2679 - val_accuracy: 0.7960
Epoch 17/50
26689/26689 [==============================] - 2s 82us/sample - loss: 1.2215 - accuracy: 0.7730 - val_loss: 1.2702 - val_accuracy: 0.8018
Epoch 18/50
26689/26689 [==============================] - 2s 83us/sample - loss: 1.2165 - accuracy: 0.7772 - val_loss: 1.2688 - val_accuracy: 0.7984
Epoch 19/50
26689/26689 [==============================] - 2s 83us/sample - loss: 1.2222 - accuracy: 0.7737 - val_loss: 1.2687 - val_accuracy: 0.7984
Epoch 20/50
26689/26689 [==============================] - 2s 82us/sample - loss: 1.2198 - accuracy: 0.7744 - val_loss: 1.2690 - val_accuracy: 0.7984


In [12]:
print('The reward associated with the best Dense Neural Network with Dropout, Classifier using roc_auc metric is: ',np.mean(scores_neural_dropout))

The reward associated with the best Dense Neural Network with Dropout, Classifier using roc_auc metric is:  0.7891805239407235


In [13]:
print('The risk associated with the best Dense Neural Network with Dropout, Classifier using roc_auc metric is: ',np.std(scores_neural_dropout))

The risk associated with the best Dense Neural Network with Dropout, Classifier using roc_auc metric is:  0.015162701997623915


In [14]:
R_R_Ratio_neural_dropout = np.mean(scores_neural_dropout)/np.std(scores_neural_dropout)

In [15]:
print('The reward risk ratio for the best Dense Neural Network with Dropout, Classifier using roc_auc metric is: ',R_R_Ratio_neural_dropout)

The reward risk ratio for the best Dense Neural Network with Dropout, Classifier using roc_auc metric is:  52.04748626362193


#### The R_R Ratio for the best Dense Neural Network (with Drop out) classifier using reduced feature set is: 52.04748626362193

## Observations:
### 1) The test set roc_auc score of the best Dense Neural Network (with Dropout) Classifier (even after employing considerably more no. of  trainable parameters) is  0.8040792755554508, slightly less than that of with Neural net with equal no. of neurons/ layer. This was expected as regularization using dropout layer gives better result in dense neural nets where overfitting is predominant, unlike shallow one here.  
### 2) The R_R ratio of the best Dense Neural Network (with Dropout) Classifier is  highest among the Dense neural net family of classifier & comparable to that of tree based bagging classifiers, due to very small 10 fold roc_auc Std_Dev. This was expected as regularization techniques such as dropout tend to reduce test set variance.
### 3) Even though the R_R ratio for Best Neural Net with Dropout is comparable to those of  Random Forest classifier, the former has high computational complexity & thus even here Random forest classifier is obvious winner.

## Model_12:  Keras Variable Layer Dense Model With SELU Activation & Alpha_Dropout layer, Utilizing  MC Alpha Dropout

In [27]:
# Extending  alpha dropout  Class
class MCAlphaDropout(keras.layers.AlphaDropout):
    def call(self, inputs):
        return super().call(inputs, training=True)

In [28]:
# Altering Best_Model_alpha for prediction
Best_Model_MC = keras.models.Sequential([
    keras.layers.InputLayer(input_shape=X_train_red.shape[1:])]+
    [MCAlphaDropout(layer.rate) if isinstance(layer, keras.layers.AlphaDropout) else layer
    for layer in Best_Model_alpha.layers
])

In [29]:
# Getting the summary of Best Model MC
Best_Model_MC.summary()

Model: "sequential_102"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_427 (Dense)            (None, 125)               4625      
_________________________________________________________________
dense_428 (Dense)            (None, 339)               42714     
_________________________________________________________________
dense_429 (Dense)            (None, 329)               111860    
_________________________________________________________________
mc_alpha_dropout (MCAlphaDro (None, 329)               0         
_________________________________________________________________
dense_430 (Dense)            (None, 1)                 330       
Total params: 159,529
Trainable params: 159,529
Non-trainable params: 0
_________________________________________________________________


In [34]:
# Compiling the Best_Model_MC best model.
Best_Model_MC.compile(loss="binary_crossentropy", optimizer=keras.optimizers.Nadam(beta_1=0.9, beta_2=0.999), metrics=["accuracy"])

In [35]:
# Assigning Best_Model_MC the weights of Model 
Best_Model_MC.set_weights(Best_Model_alpha.get_weights())

In [36]:
# Making 200 predictions over the Reduced feature test set
y_preds_mc = np.array([Best_Model_MC.predict(X_test_red) for i in range(200)])

In [37]:
# Shape of the prediction tensor
y_preds_mc.shape

(200, 8238, 1)

In [38]:
# Averaging the predictions to get new mean predictions for each instancepredictions
y_pred_mc = np.mean(y_preds_mc,axis=0)

In [39]:
print('The ROC AUC for the test set using the best MC _Dropout Keras Sequential classifier  is:',roc_auc_score(y_test, y_pred_mc))

The ROC AUC for the test set using the best MC _Dropout Keras Sequential classifier  is: 0.8038853542619935


In [47]:
# Saving the best MC Dense Model
Best_Model_MC.save('Best_model_Selu_dropout_learn_MC.h5')

## Observations:
### 1) The test set roc_auc score for the Monte carlo dropout model is slightly less than that of the alpha drop out model , indicating that the alpha drop out model fitted the dataset well. 

### R_R Ratio for the best Neural Net classifier using reduced feature set is: 52.04748626362193 , corresponding to tuned Neural net with Dropout.

### _Thus keeping everything into account (including No. of  trainable parameters & the computational costs), for this dataset , the best Neural Net classifier is tuned Dense Network with equal no. of neurons/layer._